In [1]:
import os
import pandas as pd
import folium
from folium import IFrame
import random

# folium 모듈을 이용하면 쉽게 커스텀지도를 만들 수 있습니다. 
# html파일의 형태로 바로 만들어집니다.

In [2]:

def create_map(mymap, lat, lon, zoom_start):
    min_lat=-85
    max_lat=85
    min_lon=-180
    max_lon=180
    mymap = folium.Map(location=[lat,lon], 
                                    zoom_start=zoom_start,
                                    tiles='cartodbdark_matter',
                                    max_bounds=True,
                                    min_lat=min_lat,
                                    max_lat=max_lat,
                                    min_lon=min_lon,
                                    max_lon=max_lon,
                                    max_zoom=4,
                                    min_zoom=2)
    mymap.add_child(folium.LatLngPopup())
    
    return mymap



created_mymap = None


created_mymap = create_map(created_mymap, 15.9613,206.3672,2)
#print(created_mymap)
created_mymap

# 커스텀이미지마커를 만듭니다. 그리고 그 이미지마커를 클릭하면 ifrmae태그를 이용해 html파일을 마커에 추가시킵니다 

In [3]:

def custom_img_marker(mymap, news_lat, news_lon, news_msg, news_img_link, news_link):
    news_where = [news_lat, news_lon]
    news_msg = news_msg
    news_img_link = news_img_link
    news_img = folium.features.CustomIcon(news_img_link, icon_size=(50,50))

    news_link = news_link
    news_atag ='<a href=' + news_link + ' target="_blank">see the article</a>' 

    news_iframe = IFrame(news_atag, width=100, height=50)
    news_popup = folium.Popup(news_iframe, max_width=2650, parse_html=True)

    folium.Marker(news_where,
                  tooltip=news_msg,
                  icon=news_img, 
                  popup=news_popup).add_to(mymap)

    
custom_img_marker(created_mymap, 36.4033,127.8618, 
                                    '일회용 수저 빼달랬는데 왜 자꾸 주나요',
                                    'static/orange.png',  
                                    'http://www.segye.com/newsView/20191004509710?OutUrl=Zum')

created_mymap

# image overlay를 이용해서 지도에 이미지를 겹칩니다

In [4]:

def img_overlay(mymap, gyre_img_link, bounds_list1, bounds_list2 ,popup_msg):
    
    gyre_img_link =gyre_img_link
    gyre_img = folium.raster_layers.ImageOverlay(
        name='plastic island',
        image=gyre_img_link,
        bounds=[bounds_list1, bounds_list2],
        opacity=0.4,
        interactive=True,
        cross_origin=False,
        zindex=1,
    )
    folium.Popup(popup_msg).add_to(gyre_img)

    gyre_img.add_to(mymap)
    folium.LayerControl().add_to(mymap)


img_overlay(created_mymap, 
           'static/whirlpool.png',
            [2, 160], [50, 220],
            'i am the gyre'
           )
created_mymap

# iframe에 이미지를 넣을 때는 인터넷상의 이미지를 가져오는게 렌더링이 빠르다 
# 이미지 찾는곳: https://commons.wikimedia.org/wiki/Main_Page

In [5]:

def iframe_img(mymap, resolution, width, height, img_src, lat, lan):
    html = '<img src=' + img_src + '>'
    iframe = IFrame(html, width=(width*resolution)+20, height=(height*resolution)+20)
    popup = folium.Popup(iframe, max_width=2650)

    icon = folium.Icon(color="red", icon="ok")
    marker = folium.Marker(location=[lat, lan], popup=popup, icon=icon)
    marker.add_to(mymap)


resolution, width, height = 75, 7, 3
iframe_img(created_mymap, resolution, width, height,  
           "https://upload.wikimedia.org/wikipedia/commons/f/f4/Mercator_projection_SW.jpg",
           -21.2520, 136.0329)

created_mymap
           
           

In [6]:
resolution, width, height = 75, 7, 3
iframe_img(created_mymap, resolution, width, height,  
           "https://upload.wikimedia.org/wikipedia/commons/9/91/Manchots_empereurs_tobogannent.JPG",
           -13.5452, 304.0511)


created_mymap

In [7]:
created_mymap.save('created_mymap.html')

# plastic data visualization

In [12]:
created_mymap = None
created_mymap = create_map(created_mymap, 15.9613,206.3672,2)


In [15]:
country_df = pd.read_csv('country.csv',  na_values = False)



# Share of plastic waste that is inadequately managed, 2010
csv_df = pd.read_csv('inadequately-managed-plastic.csv', na_values = False)
mismanaged_df = pd.merge(csv_df, country_df, how='outer')
#mismanaged_df.head()
mismanaged_df = mismanaged_df.fillna(0)
#mismanaged_df.head()

for i in range(0, len(mismanaged_df)):
    folium.Circle(
        location = [mismanaged_df.iloc[i]['Latitude'], mismanaged_df.iloc[i]['Longitude']],
        popup = mismanaged_df.iloc[i]['Entity'],
        radius = mismanaged_df.iloc[i]['Share of plastic inadequately managed (%)'] * 4000,
        color = 'yellow',
        fill = True,
        fill_color = 'yellow'
    ).add_to(created_mymap)

#2010 Total plastic waste by country
csv_df2 = pd.read_csv('plastic-waste-generation-total.csv', na_values = False)
waste_df = pd.merge(csv_df2, country_df, how='outer')
#waste_df.head()
waste_df = waste_df.fillna(0)

for i in range(0, len(waste_df)):
    folium.Circle(
        location = [waste_df.iloc[i]['Latitude'], waste_df.iloc[i]['Longitude']],
        popup = waste_df.iloc[i]['Entity'],
        radius = waste_df.iloc[i]['Plastic waste generation (tonnes, total) (tonnes per year)'] / 40,
        color = 'crimson',
        fill = True,
        fill_color = 'red'
    ).add_to(created_mymap)

created_mymap

In [14]:
    
def csv_data_visualization(mymap, csvfile,radius_column, color_choice):
    country_df = pd.read_csv('testmap/static/testmap/pls_data/country.csv',  na_values = False)
    csv_df = pd.read_csv(csvfile, na_values = False)
    merged_df = pd.merge(csv_df, country_df, how='outer')
    merged_df = merged_df.fillna(0)
    merged_df.head()

    for i in range(0, len(merged_df)):
        folium.Circle(
            location = [merged_df.iloc[i]['Latitude'], merged_df.iloc[i]['Longitude']],
            popup = merged_df.iloc[i]['Entity'],
            radius = merged_df.iloc[i][radius_column] * 4000,
            color =color_choice,
            fill = True,
            fill_color =color_choice,
        ).add_to(mymap)
    

created_mymap = None
created_mymap = create_map(created_mymap, 15.9613,206.3672,2)

csvfile = 'testmap/static/testmap/pls_data/inadequately-managed-plastic.csv',
radius_column = 'Share of plastic inadequately managed (%)'
color_choice =  'yellow'
csv_data_visualization(created_mymap, csvfile,radius_column, color_choice)

csvfile = 'testmap/static/testmap/pls_data/plastic-waste-generation-total.csv',
radius_column = 'Plastic waste generation (tonnes, total) (tonnes per year)'
color_choice =   'crimson',
csv_data_visualization(created_mymap, csvfile,radius_column, color_choice)

created_mymap

ValueError: Invalid file path or buffer object type: <class 'tuple'>